<a href="https://colab.research.google.com/github/cchen744/uhi-extreme-heat-response/blob/main/notebooks/03_uhi_n_landcover.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# ΔUHI & Built-environment
1. **Goal**: To investigate the possible relationship between SUHI response and built environment. Since we observed a significant increase in SUHI in several cities while others not, we are assuming that if this condition-dependence might be contributed to by composition of the built environment; we test whether this is true.

2. **Outcome Variable: Defining SUHI condition-dependence**: in this step, we define SUHI's condition-dependence as:
    
    *ΔUHI = UHI_extreme − UHI_baseline*

    - UHI_extreme: SUHI when the daily mean temperature is over 90 percentile of the daily mean temperature
    - UHI_baseline: the average of SUHI when the daily mean temperature is between 50-70 percentile.

    (Percentiles are computed within the warm-season window to ensure comparability across cities.)

3. **Explanatory Variables: Built-environment characteristics**:

    **Surface composition**:
      - Impervious surface fraction
      - Vegetation / NDVI / tree cover
      - Water or bare land fraction
      - LCZ composition

    **Urban form & intensity proxies**:
      - Built-up density / road density

4. **Analytical Strategy**
  - Analytical Unit: grid cell within each city (resolution =
  - Model:
  
    *ΔUHI_cell ~ composition_cell + proxies_cell + city fixed effects*

  - Comparison logic:
    - within-city: which built factors is correlated with ΔUHI_cell
    - across-city: does this explain why some city has higher ΔUHI
  
  - Control principles:
    - Same buffer scale
    - Same spatial resolution
    - Same seasonal window



In [45]:
!git init
!git remote add origin https://github.com/cchen744/uhi-extreme-heat-response.git
!git pull origin main --allow-unrelated-histories
!git branch -m master
!git status

Reinitialized existing Git repository in /content/.git/
error: remote origin already exists.
From https://github.com/cchen744/uhi-extreme-heat-response
 * branch            main       -> FETCH_HEAD
Already up to date.
On branch master
Your branch is ahead of 'origin/main' by 1 commit.
  (use "git push" to publish your local commits)

nothing to commit, working tree clean


fatal: could not read Username for 'https://github.com': No such device or address


In [37]:
from pathlib import Path
import os
import pandas as pd
import ee
import uhi_pipeline
import importlib
importlib.reload(uhi_pipeline)
print("uhi_pipeline module reloaded.")

ee.Authenticate()
ee.Initialize(project='extremeweatheruhi')

DATA_DIR = Path("data/city_cell")
DATA_DIR.mkdir(parents=True, exist_ok=True)

ua_fc = ee.FeatureCollection("projects/extremeweatheruhi/assets/uac20_2025")

uhi_pipeline module reloaded.


Before starting analysis, we need to get daily output on the level of grid cell due to the need for intra-city built environment analysis. In uhi_pipeline.py, the grid cell is defined as a 1km x 1km square grid projected from EPSG: 3875.

In [8]:
uhi_pipeline.select_ua(ua_fc,ua_contains="Phoenix")

In [38]:
# Example: Phoenix
df = uhi_pipeline.run_city(
    ua_fc=ua_fc,
    ua_contains="Phoenix",
    start_date="2013-07-01",
    end_date="2013-08-01",
    unit="cell", # modify unit to 'cell'
    cell_scale_m=1000,
    min_cell_pixels=1,
    min_rural_pixels=50,
    agg_func="median",
    lst_band="LST_Night_1km",
    qc_band="QC_Night",
)

print(df.shape)
print(df.head())
print(df["date"].min(), df["date"].max())
print(df[["cell_n","rural_n"]].describe())

Error fetching data: Computation timed out.
(0, 0)
Empty DataFrame
Columns: []
Index: []


KeyError: 'date'

Displaying the current content of `uhi_pipeline.py` to verify the applied changes.

In [35]:
with open('/content/uhi_pipeline.py', 'r') as f:
    print(f.read())

"""
Reusable SUHI data pipeline (GEE + MODIS LST)
Optimized Version: Uses Combined Reducers to reduce server load.
"""

import ee
import geemap
import pandas as pd
import numpy as np
from datetime import datetime
from dateutil.relativedelta import relativedelta

# ------------------------------------------------------------------
# 0. Earth Engine init
# ------------------------------------------------------------------
def init_ee():
    try:
        ee.Initialize()
    except Exception:
        ee.Authenticate()
        ee.Initialize()

# ------------------------------------------------------------------
# 1. Helper: monthly ranges
# ------------------------------------------------------------------
def month_starts(start_date, end_date):
    s = datetime.strptime(start_date, "%Y-%m-%d").replace(day=1)
    e = datetime.strptime(end_date, "%Y-%m-%d")
    cur = s
    while cur < e:
        nxt = cur + relativedelta(months=1)
        yield cur.strftime("%Y-%m-%d"), nxt.strftime("%Y-%m-%

In [39]:
!git status


On branch main
Your branch is up to date with 'origin/main'.

Changes to be committed:
  (use "git restore --staged <file>..." to unstage)
	new file:   .config/.last_opt_in_prompt.yaml
	new file:   .config/.last_survey_prompt.yaml
	new file:   .config/.last_update_check.json
	new file:   .config/active_config
	new file:   .config/config_sentinel
	new file:   .config/configurations/config_default
	new file:   .config/default_configs.db
	new file:   .config/hidden_gcloud_config_universe_descriptor_data_cache_configs.db
	new file:   .config/logs/2026.01.16/14.23.31.981136.log
	new file:   .config/logs/2026.01.16/14.24.03.314209.log
	new file:   .config/logs/2026.01.16/14.24.13.071214.log
	new file:   .config/logs/2026.01.16/14.24.18.954466.log
	new file:   .config/logs/2026.01.16/14.24.28.646070.log
	new file:   .config/logs/2026.01.16/14.24.29.392089.log
	new file:   .config/logs/2026.01.27/19.54.48.653427.log
	modified:   __pycache__/uhi_pipeline.cpython-312.pyc
	new file:   sample_data

In [40]:
!git restore --staged uhi_pipeline.py


In [41]:
!git status

On branch main
Your branch is up to date with 'origin/main'.

Changes to be committed:
  (use "git restore --staged <file>..." to unstage)
	new file:   .config/.last_opt_in_prompt.yaml
	new file:   .config/.last_survey_prompt.yaml
	new file:   .config/.last_update_check.json
	new file:   .config/active_config
	new file:   .config/config_sentinel
	new file:   .config/configurations/config_default
	new file:   .config/default_configs.db
	new file:   .config/hidden_gcloud_config_universe_descriptor_data_cache_configs.db
	new file:   .config/logs/2026.01.16/14.23.31.981136.log
	new file:   .config/logs/2026.01.16/14.24.03.314209.log
	new file:   .config/logs/2026.01.16/14.24.13.071214.log
	new file:   .config/logs/2026.01.16/14.24.18.954466.log
	new file:   .config/logs/2026.01.16/14.24.28.646070.log
	new file:   .config/logs/2026.01.16/14.24.29.392089.log
	new file:   .config/logs/2026.01.27/19.54.48.653427.log
	modified:   __pycache__/uhi_pipeline.cpython-312.pyc
	new file:   sample_data

In [42]:
!git add uhi_pipeline.py
!git commit -m "UPDATE"

[main 395b1bf] UPDATE
 23 files changed, 51082 insertions(+), 9 deletions(-)
 create mode 100644 .config/.last_opt_in_prompt.yaml
 create mode 100644 .config/.last_survey_prompt.yaml
 create mode 100644 .config/.last_update_check.json
 create mode 100644 .config/active_config
 create mode 100644 .config/config_sentinel
 create mode 100644 .config/configurations/config_default
 create mode 100644 .config/default_configs.db
 create mode 100644 .config/hidden_gcloud_config_universe_descriptor_data_cache_configs.db
 create mode 100644 .config/logs/2026.01.16/14.23.31.981136.log
 create mode 100644 .config/logs/2026.01.16/14.24.03.314209.log
 create mode 100644 .config/logs/2026.01.16/14.24.13.071214.log
 create mode 100644 .config/logs/2026.01.16/14.24.18.954466.log
 create mode 100644 .config/logs/2026.01.16/14.24.28.646070.log
 create mode 100644 .config/logs/2026.01.16/14.24.29.392089.log
 create mode 100644 .config/logs/2026.01.27/19.54.48.653427.log
 create mode 100755 sample_data/REA

In [44]:
!git status
!git push

On branch main
Your branch is ahead of 'origin/main' by 1 commit.
  (use "git push" to publish your local commits)

nothing to commit, working tree clean
fatal: could not read Username for 'https://github.com': No such device or address
